In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!nvidia-smi

Mon Dec 16 13:40:25 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA A100-SXM4-40GB          Off | 00000000:00:04.0 Off |                    0 |
| N/A   30C    P0              46W / 400W |      2MiB / 40960MiB |      0%      Default |
|                                         |                      |             Disabled |
+-----------------------------------------+----------------------+--

## Training

In [ ]:
import os
os.chdir("/content/drive/MyDrive/GuitarJam")
!git clone https://github.com/ylacombe/musicgen-dreamboothing.git
os.chdir("/content/drive/MyDrive/GuitarJam/musicgen-dreamboothing")
!pip install -e .
!pip install -U git+https://github.com/huggingface/transformers

Obtaining file:///content/drive/MyDrive/GuitarJam/musicgen-dreamboothing
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 16.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.0/84.0 kB 8.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 16.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.0 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
  Running setup.py develop for musicgen-dreamboothing
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024

In [ ]:
# !accelerate config

# # reference: https://stackoverflow.com/questions/74962932/not-able-to-select-an-option-on-google-colab
# !accelerate config default

# !mv /root/.cache/huggingface/accelerate/default_config.yaml /content/
# # edit manually then put it back
# !mv /content/default_config.yaml /root/.cache/huggingface/accelerate/
# !accelerate config update

In [ ]:
# !python dreambooth_musicgen.py --help

In [ ]:
import wandb
wandb.login()

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

 ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

### Continue Training
- `--use_lora`: state this to utilize lora.  lora configs should be edited in codebase
- `--dataset_name`: change dataset to fine-tune and perform different experiments
  - `dataset_config_name`, `--target_audio_column_name`, `--text_column_name`, `--train_split_name`, `--eval_split_name` are associated with the prepared datasets
- `--fp16`: precision to load model
- `--gradient_accumulation_steps`, `--gradient_checkpointing`: fine-tuning tricks to save VRAM
- `--overwrite_output_dir`: use `false` to continue train on model checkpoint


In [ ]:
# version 1: using pure comping data with smaller lora rank = 16
!python dreambooth_musicgen.py \
    --use_lora \
    --model_name_or_path "facebook/musicgen-melody" \
    --dataset_name "/content/drive/MyDrive/GuitarJam/audio_mono-mic/comp" \
    --dataset_config_name "default" \
    --target_audio_column_name "audio" \
    --text_column_name "prompt" \
    --train_split_name "train" \
    --eval_split_name "validation" \
    --output_dir "/content/drive/MyDrive/GuitarJam/MusicGen/guitar-solo-pretrained-c100-lora16" \
    --do_train \
    --fp16 \
    --num_train_epochs 480 \
    --gradient_accumulation_steps 8 \
    --gradient_checkpointing \
    --per_device_train_batch_size 6 \
    --learning_rate 2e-4 \
    --adam_beta1 0.9 \
    --adam_beta2 0.99 \
    --weight_decay 0.1 \
    --guidance_scale 3.0 \
    --do_eval \
    --predict_with_generate \
    --include_inputs_for_metrics \
    --eval_steps 25 \
    --evaluation_strategy "steps" \
    --per_device_eval_batch_size 4 \
    --max_eval_samples 8 \
    --generation_max_length 400 \
    --dataloader_num_workers 8 \
    --logging_steps 1 \
    --max_duration_in_seconds 30 \
    --min_duration_in_seconds 1.0 \
    --preprocessing_num_workers 8 \
    --pad_token_id 2048 \
    --decoder_start_token_id 2048 \
    --seed 456 \
    --overwrite_output_dir false


2024-12-15 10:53:17.157345: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-12-15 10:53:17.175208: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-12-15 10:53:17.197239: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-12-15 10:53:17.203763: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-12-15 10:53:17.219496: I tensorflow/core/platform/cpu_feature_guar

## Release GPU

In [ ]:
!nvidia-smi --gpu-reset  # 釋放 GPU 資源

GPU 00000000:00:04.0 is currently in use by another process.

1 device is currently being used by one or more other processes (e.g., Fabric Manager, CUDA application, graphics application such as an X server, or a monitoring application such as another instance of nvidia-smi). Please first kill all processes using this device and all compute applications running in the system.


## Inference

In [ ]:
from peft import PeftConfig, PeftModel
from transformers import AutoModelForTextToWaveform, AutoProcessor
import torch
import soundfile as sf

device = torch.device("cuda:0" if torch.cuda.device_count()>0 else "cpu")

# repo_id = "/content/drive/MyDrive/GuitarJam/MusicGen/guitar-solo-pretrained-c100-lora16"
# repo_id = "/content/drive/MyDrive/GuitarJam/MusicGen/guitar-solo-pretrained-s+c100-lora16"
repo_id = "/content/drive/MyDrive/GuitarJam/MusicGen/guitar-solo-pretrained-ca-lora32"

config = PeftConfig.from_pretrained(repo_id)
model = AutoModelForTextToWaveform.from_pretrained(config.base_model_name_or_path, torch_dtype=torch.float16)
model = PeftModel.from_pretrained(model, repo_id).to(device)

processor = AutoProcessor.from_pretrained(repo_id)

inputs = processor(
    text=[
        "High-quality acoustic guitar solo, virtuosic performance, pure guitar melody but gentle emotional depth with dynamic techniques",
        "High-quality acoustic guitar accompaniment, virtuosic performance, pure guitar melody but gentle emotional depth with dynamic techniques",
        "High-quality music with guitar, virtuosic performance, pure guitar melody but gentle emotional depth with dynamic techniques"
    ],
    padding=True,
    return_tensors="pt",
).to(device)
audio_values = model.generate(**inputs, do_sample=True, guidance_scale=3, max_new_tokens=256*5)

sampling_rate = model.config.audio_encoder.sampling_rate
audio_values = audio_values.cpu().float().numpy()
sf.write("/content/drive/MyDrive/GuitarJam/musicgen_v3_solo.wav", audio_values[0].T, sampling_rate)
sf.write("/content/drive/MyDrive/GuitarJam/musicgen_v3_comp.wav", audio_values[1].T, sampling_rate)
sf.write("/content/drive/MyDrive/GuitarJam/musicgen_v3_music.wav", audio_values[2].T, sampling_rate)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
from IPython.display import Audio

In [ ]:
Audio("/content/drive/MyDrive/GuitarJam/musicgen_lora_64_mix_1.wav")

In [ ]:
Audio("/content/drive/MyDrive/GuitarJam/musicgen_lora_64_test.wav")

In [ ]:
Audio("/content/drive/MyDrive/GuitarJam/musicgen_lora_128_test.wav")

In [ ]:
Audio("/content/drive/MyDrive/GuitarJam/musicgen_lora_512_test.wav")